# '따릉이' 자전거 조회 API를 활용한 지도 만들기

## Open API 신청

### 자료 받아오기

In [1]:
import requests
import pandas as pd

In [2]:
# apikey = ''

In [3]:
# # 최대 1천개의 데이터만 불러올 수 있음
# startnum = 1
# endnum = 1000
#
# url1 = f'http://openapi.seoul.go.kr:8088/{apikey}/json/bikeList/{startnum}/{endnum}/'
# print(url1)

In [4]:
# # 자료 요청하기
# requests.get(url1)   # Response [200] : 정상

In [5]:
# json1 = requests.get(url1).json()
# json1

In [6]:
# # 필요한 정보 선택
# json1.keys()

In [7]:
# json1['rentBikeStatus']

In [8]:
# json1['rentBikeStatus'].keys()

In [9]:
# # 데이터의 구조 확인
# json1['rentBikeStatus']['list_total_count']     # 응답한 데이터 개수

In [10]:
# json1['rentBikeStatus']['RESULT']       # 응답한 결과의 오류 여부

In [11]:
# json1['rentBikeStatus']['row']      # 자전거 정류장별 자전거 현황

In [12]:
# # 데이터 프레임으로 전환
# raw1 = pd.DataFrame(json1['rentBikeStatus']['row'])
# raw1.head()

In [13]:
# # 1001-2000번 자전거 정류장 데이터
# startnum = 1001
# endnum = 2000
#
# url2 = f'http://openapi.seoul.go.kr:8088/{apikey}/json/bikeList/{startnum}/{endnum}/'
#
# json2 = requests.get(url2).json()

In [14]:
# json2

In [15]:
# raw2 = pd.DataFrame(json2['rentBikeStatus']['row'])
# raw2.head()

In [16]:
# data = pd.concat([raw1,raw2])
# data.head()

In [17]:
# data.info()

In [18]:
# # 엑셀 파일로 저장
# data.to_excel('./data/bicycle.xlsx', index=False)

### 데이터 불러오기

In [19]:
FILE = './data/bicycle.xlsx'

data = pd.read_excel(FILE)

In [20]:
data.head()

rackTotCnt      stationName  parkingBikeTotCnt  shared  stationLatitude  \
0          15  102. 망원역 1번출구 앞                 15     100        37.555649   
1          14  103. 망원역 2번출구 앞                 28     200        37.554951   
2          13  104. 합정역 1번출구 앞                  8      62        37.550629   
3           5  105. 합정역 5번출구 앞                  2      40        37.550007   
4          12  106. 합정역 7번출구 앞                 10      83        37.548645   

   stationLongitude stationId  
0        126.910629      ST-4  
1        126.910835      ST-5  
2        126.914986      ST-6  
3        126.914825      ST-7  
4        126.912827      ST-8

## 지도시각화

In [21]:
import folium

In [22]:
# 서울역 : ['37.5536067', '126.9674308']
m = folium.Map(location=['37.5536067', '126.9674308'], zoom_start=13)
m

In [23]:
# 따릉이 지도 1
for i in data.index:
    lat = data.loc[i, 'stationLatitude']
    long = data.loc[i, 'stationLongitude']
    name = data.loc[i, 'stationName']
    available = data.loc[i, 'parkingBikeTotCnt']
    total = data.loc[i, 'rackTotCnt']
    # print(name, available, total, lat, long)

    folium.Marker(location=[lat, long],
                  tooltip=f'{name}:{available}').add_to(m)

m

In [24]:
# 따릉이 지도 2

# 자전거 수량에 대한 색상 표시
## 자전거 보유율>50%  ->  파란색
## 현재 자전거 보유량 < 2  ->  빨간색
## 그 외  -> 초록색

for i in data.index:
    lat = data.loc[i, 'stationLatitude']
    long = data.loc[i, 'stationLongitude']
    name = data.loc[i, 'stationName']
    available = data.loc[i, 'parkingBikeTotCnt']
    total = data.loc[i, 'rackTotCnt']

    # 아이콘 지정 조건
    if available/total > 0.5:
        color = 'blue'
    elif available < 2:
        color = 'red'
    else:
        color = 'green'

    icon = folium.Icon(color=color, icon='info-sign')
    folium.Marker(location=[lat, long],
                  tooltip=f'{name}:{available}',
                  icon=icon).add_to(m)

m

In [25]:
# 지도 저장하기
m.save('./map/bicycle_map.html')

##  지도시각화 (클러스터/미니맵)

In [26]:
from folium.plugins import MiniMap, MarkerCluster

In [27]:
# 따릉이 지도 3
m = folium.Map(location=['37.5536067', '126.9674308'], zoom_start=13)

# 미니맵
minimap = MiniMap()
minimap.add_to(m)

# 클러스터
marker_cluster = MarkerCluster()
m_cluster = marker_cluster.add_to(m)

for i in data.index:
    lat = data.loc[i, 'stationLatitude']
    long = data.loc[i, 'stationLongitude']
    name = data.loc[i, 'stationName']
    available = data.loc[i, 'parkingBikeTotCnt']
    total = data.loc[i, 'rackTotCnt']

    # 아이콘 지정 조건
    if available/total > 0.5:
        color = 'blue'
    elif available < 2:
        color = 'red'
    else:
        color = 'green'

    icon = folium.Icon(color=color, icon='info-sign')
    folium.Marker(location=[lat, long],
                  tooltip=f'{name}:{available}',
                  icon=icon).add_to(m_cluster)

m

In [28]:
# 저장하기

m.save('./map/bicycle_cluster.html')